# Incidence de la varicelle

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek

Les données de l'incidence du syndrome de la varicelle sont disponibles du site Web du [Réseau Sentinelles](http://www.sentiweb.fr/). Nous les récupérons sous forme d'un fichier en format CSV dont chaque ligne correspond à une semaine de la période demandée. Nous téléchargeons toujours le jeu de données complet, qui commence en 1991 et se termine avec une semaine récente.

Pour nous protéger contre une éventuelle disparition ou modification du serveur du Réseau Sentinelles, nous faisons une copie locale de ce jeux de données que nous préservons avec notre analyse. Il est inutile et même risquée de télécharger les données à chaque exécution, car dans le cas d'une panne nous pourrions remplacer nos données par un fichier défectueux. Pour cette raison, nous téléchargeons les données seulement si la copie locale n'existe pas.

In [2]:
data_url = "http://www.sentiweb.fr/datasets/incidence-PAY-7.csv"
data_file = "syndrome-varicelle.csv"

import os
import urllib.request
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

Voici l'explication des colonnes données [sur le site d'origine](https://ns.sentiweb.fr/incidence/csv-schema-v1.json):

| Nom de colonne | Libellé de colonne                                                                                                                |
|----------------|-----------------------------------------------------------------------------------------------------------------------------------|
| week           | Semaine calendaire (ISO 8601)                                                                                                     |
| indicator      | Code de l'indicateur de surveillance                                                                                              |
| inc            | Estimation de l'incidence de consultations en nombre de cas                                                                       |
| inc_low        | Estimation de la borne inférieure de l'IC95% du nombre de cas de consultation                                                     |
| inc_up         | Estimation de la borne supérieure de l'IC95% du nombre de cas de consultation                                                     |
| inc100         | Estimation du taux d'incidence du nombre de cas de consultation (en cas pour 100,000 habitants)                                   |
| inc100_low     | Estimation de la borne inférieure de l'IC95% du taux d'incidence du nombre de cas de consultation (en cas pour 100,000 habitants) |
| inc100_up      | Estimation de la borne supérieure de l'IC95% du taux d'incidence du nombre de cas de consultation (en cas pour 100,000 habitants) |
| geo_insee      | Code de la zone géographique concernée (Code INSEE) http://www.insee.fr/fr/methodes/nomenclatures/cog/                            |
| geo_name       | Libellé de la zone géographique (ce libellé peut être modifié sans préavis)                                                       |

La première ligne du fichier CSV est un commentaire, que nous ignorons en précisant `skiprows=1`.

In [3]:
raw_data = pd.read_csv(data_url, encoding = 'iso-8859-1', skiprows=1)


Y a-t-il des points manquants dans ce jeux de données ? A priori non pas de données manquantes mais vérifions-le quand même.

In [4]:
raw_data[raw_data.isnull().any(axis=1)] 

Empty DataFrame
Columns: [week, indicator, inc, inc_low, inc_up, inc100, inc100_low, inc100_up, geo_insee, geo_name]
Index: []

Aucune donnée n'est manquante, nous pouvons poursuivre notre analyse sans modifier le fichier.

In [6]:
data = raw_data.dropna().copy()
data

week  indicator    inc  inc_low  inc_up  inc100  inc100_low  \
0     202247          7   6619     3714    9524      10           6   
1     202246          7   3041     1390    4692       5           3   
2     202245          7   3827     1720    5934       6           3   
3     202244          7   4271     2231    6311       6           3   
4     202243          7   5863     3302    8424       9           5   
5     202242          7   3770     1950    5590       6           3   
6     202241          7   4177     2219    6135       6           3   
7     202240          7   4883     1472    8294       7           2   
8     202239          7   2041      331    3751       3           0   
9     202238          7   1771      419    3123       3           1   
10    202237          7   1725      499    2951       3           1   
11    202236          7   1069      178    1960       2           1   
12    202235          7   1581      400    2762       2           0   
13    202234          7   2266      788    3744       3           1   
14    202233          7   7340        0   17399      11           0   
15    202232          7   7801     4086   11516      12           6   
16    202231          7   6896     4170    9622      10           6   
17    202230          7   9039     5770   12308      14           9   
18    202229          7  14851    10060   19642      22          15   
19    202228          7  15471    11028   19914      23          16   
20    202227          7  21191    16198   26184      32          24   
21    202226          7  16854    12806   20902      25          19   
22    202225          7  22246    18011   26481      34          28   
23    202224          7  22458    18105   26811      34          27   
24    202223          7  18772    14875   22669      28          22   
25    202222          7  18916    14941   22891      29          23   
26    202221          7  20310    16307   24313      31          25   
27    202220          7  23585    19004   28166      36          29   
28    202219          7  18593    14181   23005      28          21   
29    202218          7  17851    13963   21739      27          21   
...      ...        ...    ...      ...     ...     ...         ...   
1639  199126          7  17608    11304   23912      31          20   
1640  199125          7  16169    10700   21638      28          18   
1641  199124          7  16171    10071   22271      28          17   
1642  199123          7  11947     7671   16223      21          13   
1643  199122          7  15452     9953   20951      27          17   
1644  199121          7  14903     8975   20831      26          16   
1645  199120          7  19053    12742   25364      34          23   
1646  199119          7  16739    11246   22232      29          19   
1647  199118          7  21385    13882   28888      38          25   
1648  199117          7  13462     8877   18047      24          16   
1649  199116          7  14857    10068   19646      26          18   
1650  199115          7  13975     9781   18169      25          18   
1651  199114          7  12265     7684   16846      22          14   
1652  199113          7   9567     6041   13093      17          11   
1653  199112          7  10864     7331   14397      19          13   
1654  199111          7  15574    11184   19964      27          19   
1655  199110          7  16643    11372   21914      29          20   
1656  199109          7  13741     8780   18702      24          15   
1657  199108          7  13289     8813   17765      23          15   
1658  199107          7  12337     8077   16597      22          15   
1659  199106          7  10877     7013   14741      19          12   
1660  199105          7  10442     6544   14340      18          11   
1661  199104          7   7913     4563   11263      14           8   
1662  199103          7  15387    10484   20290      27          18   
1663  199102          7  16277  

Nos données utilisent une convention inhabituelle: le numéro de
semaine est collé à l'année, donnant l'impression qu'il s'agit
de nombre entier. C'est comme ça que Pandas les interprète.
  
Un deuxième problème est que Pandas ne comprend pas les numéros de
semaine.  Il faut lui fournir les dates de début et de fin de
semaine. Nous utilisons pour cela la bibliothèque `isoweek`.

Comme la conversion des semaines est devenu assez complexe, nous
écrivons une petite fonction Python pour cela. Ensuite, nous
l'appliquons à tous les points de nos donnés. Les résultats vont
dans une nouvelle colonne 'period'.

In [7]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

data['period'] = [convert_week(yw) for yw in data['week']]

Il restent deux petites modifications à faire.

Premièrement, nous définissons les périodes d'observation
comme nouvel index de notre jeux de données. Ceci en fait
une suite chronologique, ce qui sera pratique par la suite.

Deuxièmement, nous trions les points par période, dans
le sens chronologique.

In [8]:
sorted_data = data.set_index('period').sort_index()

 Nous vérifions la cohérence des données. Entre la fin d'une période et
le début de la période qui suit, la différence temporelle doit être
zéro, ou au moins très faible. Nous laissons une "marge d'erreur"
d'une seconde.Ceci s'avère tout à fait juste sauf pour deux périodes consécutives
entre lesquelles il manque une semaine.Nous reconnaissons ces dates: c'est la semaine sans observations
que nous avions supprimées !

In [11]:
periods = sorted_data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

# Etude de l'incidence annuelle
Nous définissons la période de référence du 1er septembre de l'année $N$ au
1er septembre de l'année $N+1$. Notre tâche est un peu compliquée par le fait que l'année ne comporte
pas un nombre entier de semaines. Nous modifions donc un peu nos périodes
de référence: à la place du 1er septembre de chaque année, nous utilisons le
premier jour de la semaine qui contient le 1er septembre.Comme l'incidence de syndrome grippal est très faible en été, cette
modification ne risque pas de fausser nos conclusions.Encore un petit détail: les données commencent en décembre 1990, ce qui
rend la première année incomplète. Nous commençons donc l'analyse en 1991.
